In [ ]:
import sys
from pathlib import Path
import numpy as np
import matplotlib.pyplot as plt

triskele_path = Path('../triskele/python/')
sys.path.append(str(triskele_path.resolve()))
import triskele

In [ ]:
# Specific Utils

def DFC_filter(raster):
    raster[raster > 1e4] = raster[raster < 1e4].max()

def show(im, im_size=1, save=None):
    plt.figure(figsize=(16*im_size,3*im_size))
    plt.imshow(im)
    plt.colorbar()
    
    if save is not None:
        plt.savefig(save, bbox_inches='tight', pad_inches=1)
    
    plt.show()

def mshow(Xs, titles=None, im_size=1, save=None):
    s = len(Xs)

    plt.figure(figsize=(16*im_size,3*im_size*s))

    for i in range(s):
        plt.subplot(s,1,i+1)
        plt.imshow(Xs[i])
        
        if titles is not None:
            plt.title(titles[i])
            
        plt.colorbar()
    
    if save is not None:
        plt.savefig(save, bbox_inches='tight', pad_inches=1)
        
    plt.show()

In [ ]:
layers_files = [
    '../Data/phase1_rasters/DEM+B_C123/UH17_GEM051_TR.tif',
    '../Data/phase1_rasters/DEM_C123_3msr/UH17_GEG051_TR.tif',
    '../Data/phase1_rasters/DEM_C123_TLI/UH17_GEG05_TR.tif',
    '../Data/phase1_rasters/DSM_C12/UH17c_GEF051_TR.tif',
    '../Data/phase1_rasters/Intensity_C1/UH17_GI1F051_TR.tif',
    '../Data/phase1_rasters/Intensity_C2/UH17_GI2F051_TR.tif',
    '../Data/phase1_rasters/Intensity_C3/UH17_GI3F051_TR.tif',
    #'../Data/ground_truth/2018_IEEE_GRSS_DFC_GT_TR.tif'
]

## Define dataset dependent raster filtering

In [ ]:
def DFC_filter(raster):
    ## Remove extrem values
    #raster[raster == raster.max()] = raster[raster != raster.max()].max()
    raster[raster > 1e4] = raster[raster < 1e4].max()
    #raster[raster == np.finfo(raster.dtype).max] = raster[raster != raster.max()].max()

## Load rasters data

In [ ]:
layers = list()

for file in layers_files:
    print('Loading {}'.format(file))
    layer = triskele.read(file)
    DFC_filter(layer)
    layers.append(layer)

layers_stack = np.stack(layers, axis=2)

## Display rasters

In [ ]:
for i in range(layers_stack.shape[2]):
    plt.figure(figsize=(16*2,3*2))
    plt.imshow(layers_stack[:,:,i])
    plt.colorbar()
    plt.title(layers_files[i])
    plt.show()

## Attributes filter with TRISKELE !

In [ ]:
area = np.array([10, 100, 1e3, 1e4, 1e5])
sd   = np.array([0.5,0.9,0.99,0.999])#,1e4,1e5,5e5])
moi  = np.array([0.01,0.02,0.03,0.04,0.05,0.06,0.07,0.08,0.09,0.1,0.2,0.3,0.4,0.5,0.6,0.7,0.8,0.9,0.99])

t = triskele.Triskele(layers_stack[:,:,:2], verbose=False)
attributes_min = t.filter(tree='min-tree',
                      area=area,
                      standard_deviation=sd,
                      moment_of_inertia=moi
                     )
attributes_max = t.filter(tree='max-tree',
                      area=area,
                      standard_deviation=sd,
                      moment_of_inertia=moi
                     )

attributes_min_lbl = ['origin']
attributes_min_lbl.extend(['Thickening area {}'.format(x) for x in area])
attributes_min_lbl.extend(['Thickening σ {}'.format(x) for x in sd])
attributes_min_lbl.extend(['Thickening moment of inertia {}'.format(x) for x in sd])

attributes_max_lbl = ['origin']
attributes_max_lbl.extend(['Thinning area {}'.format(x) for x in area])
attributes_max_lbl.extend(['Thinning σ {}'.format(x) for x in sd])
attributes_max_lbl.extend(['Thinning moment of inertia {}'.format(x) for x in sd])

attributes_min.shape, attributes_max.shape

In [ ]:
attributes     = np.dstack((attributes_min[:,:,:0:-1], attributes_max))
attributes_lbl = attributes_min_lbl[:0:-1]
attributes_lbl.extend(attributes_max_lbl)

attributes.shape, attributes_lbl

In [ ]:
figs = list()

attributes[0,0,:] = 255 # J'ai honte...

for i in range(attributes.shape[-1]):
    figs.append(attributes[:,:,i])

mshow(figs, attributes_lbl, 2)

In [ ]:
f = plt.Figure(figsize=(16,9))
f.imshow(attributes[:,:,0])
f.plt.show()

In [ ]:
show(attributes[:,:,17])

In [ ]:
{'I_{{{}}}'.format(42)}